# Port of Rotterdam - OpenTNSim

In [1]:
import opentnsim

from importlib import reload 
opentnsim = reload(opentnsim) 

In [2]:
# package(s) related to time, space and id
import datetime, time
import platform
import random
import os
import pathlib
import io
import urllib
import tempfile
import functools
import logging
import pickle
import pytz

# package(s) related to the simulation
import simpy
import networkx as nx  

# spatial libraries 
import shapely.geometry
import shapely.wkt
import pyproj
import shapely.geometry
from osgeo import ogr, osr
from simplekml import Kml, Style
import folium
import yaml

# package(s) for data handling
import requests
import math             
import json
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

logging.basicConfig(level=logging.INFO)
logger = logging.getLogger()

# define the coorinate system
geod = pyproj.Geod(ellps="WGS84")

In [3]:
# Link to the latest version of the 'Vaarweginformatie.nl' network
#url = 'https://zenodo.org/record/3981105/files/network_digital_twin_v0.1.yaml'
url = 'https://zenodo.org/record/4578289/files/network_digital_twin_v0.2.yaml'

In [4]:
# Link to vessel database
location_vessel_database = "Vessels/Vessel-database-2.csv"

## 0. Load useful methods

### A) Network functions
I think Fedor included working with the FIS in another version of OpenTNSim (for the P&W exercise) -- need to check

In [5]:
@functools.lru_cache
def load_fis_network(url):
    """load the topological fairway information system network (vaarweginformatie.nl)"""

    # get the data from the url
    resp = requests.get(url)
    # convert to file object
    stream = io.StringIO(resp.text)
    
    # This will take a minute or two
    # Here we convert the network to a networkx object
    G = nx.read_yaml(stream)
    
#     with open(url, 'r') as fh:
#         G = yaml.load(fh, Loader=yaml.Loader)

    # some brief info
    n_bytes = len(resp.content)
    msg = '''Loaded network from {url} file size {mb:.2f}MB. Network has {n_nodes} nodes and {n_edges} edges.'''
    summary = msg.format(url=url, mb=n_bytes / 1000**2, n_edges=len(G.edges), n_nodes=len(G.nodes))
    logger.info(summary)

    # The topological network contains information about the original geometry. 
    # Let's convert those into python shapely objects for easier use later
    for n in G.nodes:
        G.nodes[n]['geometry'] = shapely.geometry.Point(G.nodes[n]['X'], G.nodes[n]['Y'])
    for e in G.edges:
        edge = G.edges[e]
        edge['geometry'] = shapely.wkt.loads(edge['Wkt'])
        edge['length'] = edge_length(edge)    
    
    return G 

In [6]:
def find_closest_node(G, point):
    """find the closest node on the graph from a given point"""
    
    distance = np.full((len(G.nodes)), fill_value=np.nan)
    for ii, n in enumerate(G.nodes):
        distance[ii] = point.distance(G.nodes[n]['geometry'])
    name_node = list(G.nodes)[np.argmin(distance)]
    distance_node = np.min(distance)
    
    return name_node, distance_node

In [7]:
def find_closest_edge(G, point):
    """find the closest edge on the graph from a given point"""
    
    distance = np.full((len(G.edges)), fill_value=np.nan)
    for ii, e in enumerate(G.edges):
        distance[ii] = point.distance(G.edges[e]['geometry'])
    name_edge = list(G.edges)[np.argmin(distance)]
    distance_edge = np.min(distance)
    
    return name_edge, distance_edge

In [8]:
def edge_length(edge):
    """compute the great circle length of an edge
    The network version 0.1 contains the lat/lon distance in a length property. 
    But we need the "great circle" or projected distance. 
    Let's define a function to recompute it.
    """
    
    # get the geometry
    geom = edge['geometry']
    # get lon, lat
    lats, lons = np.array(geom).T
    # this requires pyproj 2.3.0
    distance = geod.line_length(lons, lats)

    return distance

### 1. Load Vaarweginformatie.nl graph (saved with PoR features)

In [9]:
# create a cached version to speed up loading (remove cached file if a better yaml file is available)
fname = "fis_wdata/FIS_wdata.pkl"
#fname = "fis_cache/FIS.pkl"

if os.path.exists(fname):
    print('I am loading cached network')
    with open(fname, 'rb') as pkl_file:
        FG = pickle.load(pkl_file)
        pkl_file.close()

else:
    print('I am getting new network')
    FG = load_fis_network(url)

    os.makedirs(os.path.dirname(fname), exist_ok=True)
    with open(fname, 'wb') as pkl_file:
        pickle.dump(FG, pkl_file)
        pkl_file.close()

I am loading cached network


#### 1.3 Plot the entire network

In [10]:
# Plot the network 
m = folium.Map(location=[51.9, 4.4], zoom_start = 11, tiles="cartodbpositron")

for edge in FG.edges(data = True):
    points_x = list(edge[2]["geometry"].coords.xy[0])
    points_y = list(edge[2]["geometry"].coords.xy[1])
    
    line = []
    for i, _ in enumerate(points_x):
        line.append((points_y[i], points_x[i]))
        
    folium.PolyLine(line, weight = 2, popup = (edge[2]["StartJunctionId"], edge[2]["EndJunctionId"])).add_to(m)

m

### 2. Prepare vessel objects

In [11]:
sim_start_time = datetime.datetime(2019, 1, 1, 0, 0, tzinfo=datetime.timezone.utc)
sim_start_time

datetime.datetime(2019, 1, 1, 0, 0, tzinfo=datetime.timezone.utc)

#### 2.1 Load vessel database

In [12]:
# import the route information
df_trips = pd.read_parquet('03_vessels/df_3epet.parquet')
df_trips = df_trips[df_trips['vessellength']>150]

In [13]:
for i, path in enumerate(df_trips['path']): 
    newpath = []
    for node in path: 
        try: 
            newpath.append(float(node))
        except: 
            newpath.append(node)
    df_trips.at[df_trips.index[i], 'path'] = newpath

In [14]:
for i, speed in enumerate(df_trips['speed']):
    df_trips.at[df_trips.index[i], 'speed'] = list(speed)

In [15]:
# Example calculations UKC and FWA over route
iship = df_trips.index[0]
path = df_trips.loc[iship, 'path']
T_s = df_trips.loc[iship, 'draughtMarine']
direction = 'inbound'

for i in range(1,len(path)):
    edge = path[i-1], path[i]
    
    if FG.has_edge(edge[0], edge[1]):
        # FWA
        FWA = T_s * FG.edges[edge]['FWA']
        
        # UKC
        if T_s < 17.4: 
            UKC_a = FG.edges[edge]['UKC_a (T<17.4)']
        else: 
            UKC_a = FG.edges[edge]['UKC_a (T>=17.4)']
            
        if direction == 'outbound':
            UKC_b = FG.edges[edge]['UKC_b (outbound)']
        else: 
            UKC_b = FG.edges[edge]['UKC_b (outbound)']
        UKC = UKC_a + UKC_b*T_s
        
    else: 
        FWA = float('nan')
        UKC = float('nan')
    print('edge {}: UKC = {}, FWA = {}'.format(edge, UKC, FWA))

edge (8864185.0, 8866260.0): UKC = 1.0, FWA = 0.09800000190734863
edge (8866260.0, 8864288.0): UKC = 1.0, FWA = 0.09800000190734863
edge (8864288.0, 8861022.0): UKC = 1.0, FWA = 0.09800000190734863
edge (8861022.0, 8860701.0): UKC = 1.0, FWA = 0.09800000190734863
edge (8860701.0, 8864748.0): UKC = 1.0, FWA = 0.09800000190734863
edge (8864748.0, 8865822.0): UKC = 1.0, FWA = 0.09800000190734863
edge (8865822.0, 8866305.0): UKC = 1.0, FWA = 0.09800000190734863
edge (8866305.0, 8864266.0): UKC = 0.9800000190734863, FWA = 0.09800000190734863
edge (8864266.0, 8862925.0): UKC = 0.9800000190734863, FWA = 0.09800000190734863
edge (8862925.0, 8864465.0): UKC = 0.9800000190734863, FWA = 0.09800000190734863
edge (8864465.0, 'S14716_B'): UKC = 0.9800000190734863, FWA = 0.09800000190734863
edge ('S14716_B', 'S14716_A'): UKC = 0.9800000190734863, FWA = 0.09800000190734863
edge ('S14716_A', 8860845.0): UKC = 0.9800000190734863, FWA = 0.09800000190734863
edge (8860845.0, 8861674.0): UKC = 0.98000001907

#### 2.2 Create multiple vessel objects with the new mixins, and use this in the vessel generator

In [16]:
# Make a class out of mix-ins
TransportResource = type('TransportResource', 
                         (opentnsim.core.Identifiable, opentnsim.core.ContainerDependentMovable, 
                          opentnsim.core.HasResource, opentnsim.core.Routeable, 
                          opentnsim.core.VesselProperties, opentnsim.energy_consumption_module.ConsumesEnergy), {})


In [17]:
# For testing purposes: default v = v_empty
def compute_v_provider(v_empty, v_full):
    return lambda x: v_empty

In [18]:
df_trips.drop(index=4173, inplace=True)

In [19]:
df_trips

shipname                 starttime      delay  vessellength  \
500    testschip-3799 2019-01-02 07:28:00+00:00   113280.0         182.0   
536    testschip-5953 2019-01-04 09:39:49+00:00   293989.0         229.0   
1821   testschip-6735 2019-01-02 21:46:28+00:00   164788.0         179.0   
1822   testschip-6735 2019-01-03 09:39:34+00:00   207574.0         179.0   
1824   testschip-6735 2019-01-17 01:45:40+00:00  1388740.0         179.0   
...               ...                       ...        ...           ...   
5173  testschip-11583 2019-01-13 00:59:21+00:00  1040361.0         213.0   
5404  testschip-12927 2019-01-16 02:09:48+00:00  1303788.0         186.0   
5405  testschip-12927 2019-01-17 10:29:21+00:00  1420161.0         186.0   
5449  testschip-12440 2019-01-14 17:25:48+00:00  1185948.0         178.0   
5450  testschip-12440 2019-01-16 05:01:33+00:00  1314093.0         178.0   

      vesselwidth  vesseltypeERI  draughtMarine  \
500          46.0            0.0            9.8   
536          38.0            0.0            7.0   
1821         26.0            0.0            6.8   
1822         26.0            0.0            7.0   
1824         26.0            0.0            7.0   
...           ...            ...            ...   
5173         32.0            0.0            NaN   
5404         32.0            0.0            9.2   
5405         32.0            0.0            7.6   
5449         28.0            0.0            9.0   
5450         28.0            0.0            9.0   

                                                   path  \
500   [8864185.0, 8866260.0, 8864288.0, 8861022.0, 8...   
536   [8868083.0, 8863475.0, 8865217.0, 8860596.0, 8...   
1821  [8860614.0, B5729_A, B5729_B, 8867449.0, 88623...   
1822  [8866859.0, 8866999.0, 8867980.0, 8867547.0, 8...   
1824  [8864283.0, 8860614.0, B5729_A, B5729_B, 88674...   
...                                                 ...   
5173  [8865217.0, 8860596.0, 8867980.0, 8867547.0, 8...   
5404  [8866305.0, 8864266.0, 8862925.0, 8864465.0, S...   
5405  [8868178.0, 8866999.0, 8867980.0, 8867547.0, 8...   
5449  [8866305.0, 8864266.0, 8862925.0, 8864465.0, S...   
5450  [8863090.0, 8863475.0, 8865217.0, 8860596.0, 8...   

                                                  speed  \
500   [9.677133344147908, 8.37286310540504, 9.999801...   
536   [7.857539643698429, 7.787329519608238, 7.24075...   
1821  [4.9633746885987735, 10.484369571697076, 13.07...   
1822  [9.848134545748662, 12.629315404453287, 15.410...   
1824  [5.591261482718618, 8.771800775328975, 11.6215...   
...                                                 ...   
5173  [7.3859731982377586, 8.449406837862611, 6.7650...   
5404  [16.472284281574385, 15.638895626922189, 15.02...   
5405  [6.547758925628303, 6.681213181473527, 7.23835...   
5449  [15.9223687902327, 15.312662431582705, 16.2901...   
5450  [4.9496380660952815, 7.904854047345543, 8.2055...   

                                                  times  
500   [0 days 00:02:09, 0 days 00:02:11, 0 days 00:0...  
536   [0 days 00:03:23, 0 days 00:07:40, 0 days 00:0...  
1821  [0 days 00:00:11, 0 days 00:14:59, 0 days 00:0...  
1822  [0 days 00:06:00, 0 days 00:00:00, 0 days 00:0...  
1824  [0 days 00:05:49, 0 days 00:00:11, 0 days 00:1...  
...                                                 ...  
5173  [0 days 00:03:21, 0 days 00:00:19, 0 days 00:0...  
5404  [0 days 00:10:32, 0 days 00:00:30, 0 days 00:1...  
5405  [0 days 00:08:52, 0 days 00:00:39, 0 days 00:0...  
5449  [0 days 00:11:00, 0 days 00:00:20, 0 days 00:1...  
5450  [0 days 00:04:57, 0 days 00:07:09, 0 days 00:0...  

[69 rows x 10 columns]

In [20]:
# identify which vessel type to extract from the vessel database (change the name to change the vessel used)
vessels = []
delays = []

for i_vessel in df_trips.index:

    # path and route info
    path = df_trips['path'].loc[i_vessel]
    v_list = df_trips['speed'].loc[i_vessel]

    if len(path) - len(v_list) != 1: 
        print('Path and velocities input length incorrect (difference = {} and should be 1)'.format(len(path) - len(v_list)))

    start_point = path[0]

    # prepare data for the vessel
    data_vessel = {"env": None,
                   "name": df_trips['shipname'].loc[i_vessel],
                   "route": df_trips['path'].loc[i_vessel],
                   "geometry": FG.nodes[start_point]['geometry'],
                   "capacity": 1000,
                   "compute_v": compute_v_provider(v_empty=v_list, v_full=v_list),
                   "type": df_trips['vesseltypeERI'].loc[i_vessel],
                   "B": df_trips['vesselwidth'].loc[i_vessel],
                   "L": df_trips['vessellength'].loc[i_vessel],
                   "T_e": df_trips['draughtMarine'].loc[i_vessel],
                   "T_f": df_trips['draughtMarine'].loc[i_vessel],
                   "H_e": 10,
                   "H_f": 5,
                   "P_installed": 500,
                   "L_w": 1,
                   "C_b": 0.85
                  }
    
    vessel = TransportResource(**data_vessel)
    vessels.append(vessel)
    delays.append(df_trips['delay'].loc[i_vessel])


The construction year of the engine is 2017
The construction year of the engine is 1997
The construction year of the engine is 1969
The construction year of the engine is 2010
The construction year of the engine is 1989
The construction year of the engine is 2005
The construction year of the engine is 2004
The construction year of the engine is 2003
The construction year of the engine is 2015
The construction year of the engine is 2011
The construction year of the engine is 1987
The construction year of the engine is 1994
The construction year of the engine is 2009
The construction year of the engine is 2012
The construction year of the engine is 2011
The construction year of the engine is 1976
The construction year of the engine is 1986
The construction year of the engine is 2005
The construction year of the engine is 2016
The construction year of the engine is 2004
The construction year of the engine is 1983
The construction year of the engine is 2008
The construction year of the eng

# 3. Create environment

In [21]:
# sim.add_vessels(origin,destination,[],vessel)

In [22]:
# # specify start time and duration
# simulation_start = sim_start_time 
# duration = 5*12.5*60*60 #seconds

# # create simulation with environment
# sim = model.Simulation(simulation_start,FG)
# env = sim.environment




# sim.run(duration = duration)

In [23]:
# sim.add_vessels(origin,destination,[],vessel)

In [24]:
# simulation_start = datetime.datetime.now()
# sim = model.Simulation(simulation_start,FG)
# env = sim.environment
# duration = 5*12.5*60*60 #seconds

# sim.run(duration = duration)

In [25]:
# # Start simpy environment (at a given date and time) (simulation_start = datetime.datetime.now() to just start now)
# simulation_start = sim_start_time # <============ start time
# env = simpy.Environment(initial_time = time.mktime(simulation_start.timetuple()))
# env.epoch = time.mktime(simulation_start.timetuple())

# # Add graph to environment
# env.FG = FG 

# 4. Run simulation

In [21]:
def start(env, vessel, delay):
    """The start process moves a vessel over the network 
    (from its 'vessel.geometry' position to the end of 'vessel.route')"""
    yield env.timeout(delay)
    
    vessel.log_entry("Start sailing", env.now, "", vessel.geometry)
    yield from vessel.move()
    vessel.log_entry("Stop sailing", env.now, "", vessel.geometry)
        

In [82]:
# i = 1
# simulation_start = sim_start_time # <============ start time
# env = simpy.Environment(initial_time = time.mktime(simulation_start.timetuple()))
# env.epoch = time.mktime(simulation_start.timetuple())

# # Add graph to environment
# env.FG = FG 

# # Add environment to vessel
# vessel.env = env

# # Add the movements of the vessel to the simulation
# delay = delays[i]
# vessel = vessels[i]
# env.process(start(env, vessel, delay))

# env.run()

# df_log_1 = pd.DataFrame.from_dict(vessel.log)

In [22]:
for i, vessel in enumerate(vessels):
    
    print('')
    print('i = {}'.format(i))
    
    # Start simpy environment (at a given date and time) (simulation_start = datetime.datetime.now() to just start now)
    simulation_start = sim_start_time # <============ start time
    env = simpy.Environment(initial_time = time.mktime(simulation_start.timetuple()))
    env.epoch = time.mktime(simulation_start.timetuple())

    # Add graph to environment
    env.FG = FG 
    
    # Add environment to vessel
    vessel.env = env
    
    # Add the movements of the vessel to the simulation
    delay = delays[i]
    env.process(start(env, vessel, delay))

    env.run()
    
    df_log_i = pd.DataFrame.from_dict(vessel.log)

    if i == 0: 
        df_log = df_log_i.copy()
    else: 
        df_log = pd.concat([df_log, df_log_i])


i = 0
origin = 8864185.0, destination = 8866260.0
inode = 0, speed = 9.677133344147908, name = testschip-3799
inode = 0, speed = 9.677133344147908, name = testschip-3799
origin = 8866260.0, destination = 8864288.0
inode = 1, speed = 8.37286310540504, name = testschip-3799
origin = 8864288.0, destination = 8861022.0
inode = 2, speed = 9.999801663280463, name = testschip-3799
origin = 8861022.0, destination = 8860701.0
inode = 3, speed = 11.913194479887572, name = testschip-3799
origin = 8860701.0, destination = 8864748.0
inode = 4, speed = 11.85613170449574, name = testschip-3799
origin = 8864748.0, destination = 8865822.0
inode = 5, speed = 6.982264984343468, name = testschip-3799
origin = 8865822.0, destination = 8866305.0
inode = 6, speed = 9.585292384481876, name = testschip-3799
inode = 6, speed = 9.585292384481876, name = testschip-3799
origin = 8866305.0, destination = 8864266.0
inode = 7, speed = 13.107211384265765, name = testschip-3799
origin = 8864266.0, destination = 886292

inode = 12, speed = 17.002970074146052, name = testschip-6735
inode = 12, speed = 17.002970074146052, name = testschip-6735
origin = 8864748.0, destination = 8865822.0
inode = 13, speed = 13.92427600274478, name = testschip-6735
origin = 8865822.0, destination = 8866305.0
inode = 14, speed = 10.845581931343508, name = testschip-6735
inode = 14, speed = 10.845581931343508, name = testschip-6735
origin = 8866305.0, destination = 8864266.0
inode = 15, speed = 19.53818206949179, name = testschip-6735
origin = 8864266.0, destination = 8862925.0
inode = 16, speed = 20.953018821917645, name = testschip-6735
inode = 16, speed = 20.953018821917645, name = testschip-6735
inode = 16, speed = 20.953018821917645, name = testschip-6735
origin = 8862925.0, destination = 8864465.0
inode = 17, speed = 21.43226353904218, name = testschip-6735
origin = 8864465.0, destination = S14716_B
inode = 18, speed = 21.30018409488337, name = testschip-6735
inode = 18, speed = 21.30018409488337, name = testschip-673

inode = 3, speed = 20.79202643089169, name = testschip-6457
inode = 3, speed = 20.79202643089169, name = testschip-6457
inode = 3, speed = 20.79202643089169, name = testschip-6457
inode = 3, speed = 20.79202643089169, name = testschip-6457
inode = 3, speed = 20.79202643089169, name = testschip-6457
inode = 3, speed = 20.79202643089169, name = testschip-6457
inode = 3, speed = 20.79202643089169, name = testschip-6457
inode = 3, speed = 20.79202643089169, name = testschip-6457
inode = 3, speed = 20.79202643089169, name = testschip-6457
inode = 3, speed = 20.79202643089169, name = testschip-6457
inode = 3, speed = 20.79202643089169, name = testschip-6457
inode = 3, speed = 20.79202643089169, name = testschip-6457
inode = 3, speed = 20.79202643089169, name = testschip-6457
inode = 3, speed = 20.79202643089169, name = testschip-6457
origin = 8860845.0, destination = S14716_A
inode = 4, speed = 20.50997949104672, name = testschip-6457
inode = 4, speed = 20.50997949104672, name = testschip-64

inode = 8, speed = 19.213530693069, name = testschip-5637
inode = 8, speed = 19.213530693069, name = testschip-5637
origin = S14716_A, destination = S14716_B
inode = 9, speed = 22.63918845378935, name = testschip-5637
origin = S14716_B, destination = 8864465.0
inode = 10, speed = 19.81913252504507, name = testschip-5637
inode = 10, speed = 19.81913252504507, name = testschip-5637
inode = 10, speed = 19.81913252504507, name = testschip-5637
inode = 10, speed = 19.81913252504507, name = testschip-5637
origin = 8864465.0, destination = 8862925.0
inode = 11, speed = 23.000470628768568, name = testschip-5637
origin = 8862925.0, destination = 8864266.0
inode = 12, speed = 24.436562488366707, name = testschip-5637
inode = 12, speed = 24.436562488366707, name = testschip-5637
inode = 12, speed = 24.436562488366707, name = testschip-5637

i = 14
origin = 8866305.0, destination = 8865822.0
inode = 0, speed = 21.35264444084305, name = testschip-8110
inode = 0, speed = 21.35264444084305, name = te

inode = 11, speed = 22.786246781016267, name = testschip-6043
origin = S14716_B, destination = 8864465.0
inode = 12, speed = 22.412586580107643, name = testschip-6043
inode = 12, speed = 22.412586580107643, name = testschip-6043
inode = 12, speed = 22.412586580107643, name = testschip-6043
inode = 12, speed = 22.412586580107643, name = testschip-6043
origin = 8864465.0, destination = 8862925.0
inode = 13, speed = 21.909792276797948, name = testschip-6043
origin = 8862925.0, destination = 8864266.0
inode = 14, speed = 22.534172462431368, name = testschip-6043
inode = 14, speed = 22.534172462431368, name = testschip-6043
inode = 14, speed = 22.534172462431368, name = testschip-6043

i = 19
origin = 8863275.0, destination = 8864002.0
inode = 0, speed = 9.368778780182174, name = testschip-8385
inode = 0, speed = 9.368778780182174, name = testschip-8385
origin = 8864002.0, destination = 8861067.0
inode = 1, speed = 9.4305168244907, name = testschip-8385
origin = 8861067.0, destination = 886

...

inode = 8, speed = 25.083290763936912, name = testschip-10756
origin = 8864266.0, destination = 8862925.0
inode = 9, speed = 19.554992669673787, name = testschip-10756
inode = 9, speed = 19.554992669673787, name = testschip-10756
inode = 9, speed = 19.554992669673787, name = testschip-10756
origin = 8862925.0, destination = 8864465.0
inode = 10, speed = 22.306003468771483, name = testschip-10756
origin = 8864465.0, destination = S14716_B
inode = 11, speed = 25.70109113151303, name = testschip-10756
inode = 11, speed = 25.70109113151303, name = testschip-10756
inode = 11, speed = 25.70109113151303, name = testschip-10756
inode = 11, speed = 25.70109113151303, name = testschip-10756
origin = S14716_B, destination = S14716_A
inode = 12, speed = 27.12640206990282, name = testschip-10756
origin = S14716_A, destination = 8860845.0
inode = 13, speed = 26.50347046969723, name = testschip-10756
inode = 13, speed = 26.50347046969723, name = testschip-10756
origin = 8860845.0, destination = 88616

inode = 5, speed = 24.175157830808523, name = testschip-7363
inode = 5, speed = 24.175157830808523, name = testschip-7363
inode = 5, speed = 24.175157830808523, name = testschip-7363
inode = 5, speed = 24.175157830808523, name = testschip-7363
inode = 5, speed = 24.175157830808523, name = testschip-7363
inode = 5, speed = 24.175157830808523, name = testschip-7363
inode = 5, speed = 24.175157830808523, name = testschip-7363
inode = 5, speed = 24.175157830808523, name = testschip-7363
origin = 8860845.0, destination = S14716_A
inode = 6, speed = 25.94349528636621, name = testschip-7363
inode = 6, speed = 25.94349528636621, name = testschip-7363
origin = S14716_A, destination = S14716_B
inode = 7, speed = 21.353704061122173, name = testschip-7363
origin = S14716_B, destination = 8864465.0
inode = 8, speed = 25.01436692620378, name = testschip-7363
inode = 8, speed = 25.01436692620378, name = testschip-7363
inode = 8, speed = 25.01436692620378, name = testschip-7363
inode = 8, speed = 25.0

inode = 5, speed = 19.972760748707813, name = testschip-8397
inode = 5, speed = 19.972760748707813, name = testschip-8397
inode = 5, speed = 19.972760748707813, name = testschip-8397
inode = 5, speed = 19.972760748707813, name = testschip-8397
inode = 5, speed = 19.972760748707813, name = testschip-8397
inode = 5, speed = 19.972760748707813, name = testschip-8397
inode = 5, speed = 19.972760748707813, name = testschip-8397
inode = 5, speed = 19.972760748707813, name = testschip-8397
origin = 8860845.0, destination = S14716_A
inode = 6, speed = 19.95759752534945, name = testschip-8397
inode = 6, speed = 19.95759752534945, name = testschip-8397
origin = S14716_A, destination = S14716_B
inode = 7, speed = 19.84903149559888, name = testschip-8397
origin = S14716_B, destination = 8864465.0
inode = 8, speed = 16.010979840169778, name = testschip-8397
inode = 8, speed = 16.010979840169778, name = testschip-8397
inode = 8, speed = 16.010979840169778, name = testschip-8397
inode = 8, speed = 16

inode = 8, speed = 19.261458801977696, name = testschip-12011
inode = 8, speed = 19.261458801977696, name = testschip-12011
inode = 8, speed = 19.261458801977696, name = testschip-12011
inode = 8, speed = 19.261458801977696, name = testschip-12011
inode = 8, speed = 19.261458801977696, name = testschip-12011
inode = 8, speed = 19.261458801977696, name = testschip-12011
inode = 8, speed = 19.261458801977696, name = testschip-12011
inode = 8, speed = 19.261458801977696, name = testschip-12011
inode = 8, speed = 19.261458801977696, name = testschip-12011
inode = 8, speed = 19.261458801977696, name = testschip-12011
inode = 8, speed = 19.261458801977696, name = testschip-12011
inode = 8, speed = 19.261458801977696, name = testschip-12011
origin = 8860845.0, destination = S14716_A
inode = 9, speed = 20.390620048070094, name = testschip-12011
inode = 9, speed = 20.390620048070094, name = testschip-12011
origin = S14716_A, destination = S14716_B
inode = 10, speed = 18.38172753692813, name = t

inode = 5, speed = 6.404531124899903, name = testschip-12440
origin = 8867980.0, destination = 8867547.0
inode = 6, speed = 6.643018143790668, name = testschip-12440
origin = 8867547.0, destination = 8861158.0
inode = 7, speed = 14.790402192794437, name = testschip-12440
origin = 8861158.0, destination = 8861674.0
inode = 8, speed = 18.99287989965449, name = testschip-12440
inode = 8, speed = 18.99287989965449, name = testschip-12440
inode = 8, speed = 18.99287989965449, name = testschip-12440
inode = 8, speed = 18.99287989965449, name = testschip-12440
inode = 8, speed = 18.99287989965449, name = testschip-12440
inode = 8, speed = 18.99287989965449, name = testschip-12440
inode = 8, speed = 18.99287989965449, name = testschip-12440
inode = 8, speed = 18.99287989965449, name = testschip-12440
origin = 8861674.0, destination = 8860845.0
inode = 9, speed = 21.32866184960463, name = testschip-12440
inode = 9, speed = 21.32866184960463, name = testschip-12440
inode = 9, speed = 21.32866184

# 5. Evaluate output

### 5.1 Create an output dataframe

In [23]:
# create new dataframe with useful run information

df_newlog = pd.DataFrame(columns=['Vessel name', 'Seq', 'From node', 'To node', 'Sub edge', 'Timestamp', 'From geometry', 'To geometry', 'Duration', 'Distance', 'Speed'])

for i in range(1,len(df_log.index)): 
        
    # message 
    message = df_log['Message'].iloc[i].split()
    if (message[-1] == 'start') and (len(message)>3):

        # determine duration and distance
        duration = (df_log['Timestamp'].iloc[i+1] - df_log['Timestamp'].iloc[i]).total_seconds()
        distance = geod.inv(df_log['Geometry'].iloc[i].x, df_log['Geometry'].iloc[i].y, 
            df_log['Geometry'].iloc[i+1].x, df_log['Geometry'].iloc[i+1].y)[2]
        speed = distance / duration
        try: 
            edge0 = float(message[3])
        except: 
            edge0 = message[3]
        try: 
            edge1 = float(message[6])
        except: 
            edge1 = message[6]
            
            
        df_newlog = df_newlog.append({'Vessel name': df_log['Value'].iloc[i], 'Seq': df_log.index[i], 
                                      'From node': edge0, 'To node': edge1, 'Sub edge': message[9],
                                      'Timestamp': df_log['Timestamp'].iloc[i], 
                                      'From geometry': df_log['Geometry'].iloc[i], 'To geometry': df_log['Geometry'].iloc[i+1],
                                      'Duration': duration, 'Distance': distance, 'Speed': speed}, ignore_index=True)

In [24]:
df_newlog

Vessel name Seq    From node      To node Sub edge  \
0      testschip-3799   1  8.86418e+06  8.86626e+06        0   
1      testschip-3799   3  8.86418e+06  8.86626e+06        1   
2      testschip-3799   5  8.86626e+06  8.86429e+06        0   
3      testschip-3799   7  8.86429e+06  8.86102e+06        0   
4      testschip-3799   9  8.86102e+06   8.8607e+06        0   
...               ...  ..          ...          ...      ...   
3029  testschip-12440  77     S14716_B  8.86446e+06        3   
3030  testschip-12440  79  8.86446e+06  8.86292e+06        0   
3031  testschip-12440  81  8.86292e+06  8.86427e+06        0   
3032  testschip-12440  83  8.86292e+06  8.86427e+06        1   
3033  testschip-12440  85  8.86292e+06  8.86427e+06        2   

                      Timestamp                              From geometry  \
0    2019-01-02 07:28:00.000000  POINT (4.06577726721752 51.9616878496712)   
1    2019-01-02 07:28:37.377858  POINT (4.07100475643483 51.9620610945492)   
2    2019-01-02 07:29:45.827771  POINT (4.08059629478063 51.9614848708232)   
3    2019-01-02 07:30:29.459412  POINT (4.08588733128925 51.9611749800546)   
4    2019-01-02 07:31:16.708295  POINT (4.08745551582984 51.9653093741552)   
...                         ...                                        ...   
3029 2019-01-16 05:21:03.000968  POINT (4.12542158771241 51.9731028973176)   
3030 2019-01-16 05:21:07.351999  POINT (4.12423582717078 51.9734347697144)   
3031 2019-01-16 05:21:12.661157  POINT (4.12285425403692 51.9738214268566)   
3032 2019-01-16 05:22:14.010849  POINT (4.10714114771394 51.9781909994644)   
3033 2019-01-16 05:23:42.182713   POINT (4.0841372668255 51.9838622952073)   

                                    To geometry   Duration     Distance  \
0     POINT (4.07100475643483 51.9620610945492)  37.377858   361.710519   
1     POINT (4.08059629478063 51.9614848708232)  68.449913   662.398934   
2     POINT (4.08588733128925 51.9611749800546)  43.631641   365.321756   
3     POINT (4.08745551582984 51.9653093741552)  47.248883   472.479456   
4     POINT (4.09002397683758 51.9721065878619)  65.190782   776.630463   
...                                         ...        ...          ...   
3029  POINT (4.12423582717078 51.9734347697144)   4.351031    89.460773   
3030  POINT (4.12285425403692 51.9738214268566)   5.309158   104.232441   
3031  POINT (4.10714114771394 51.9781909994644)  61.349692  1184.136286   
3032   POINT (4.0841372668255 51.9838622952073)  88.171864  1701.842355   
3033  POINT (4.08355198540297 51.9839636810505)   2.163717    41.762818   

          Speed  
0      9.677133  
1      9.677133  
2      8.372863  
3      9.999802  
4     11.913194  
...         ...  
3029  20.560822  
3030  19.632575  
3031  19.301422  
3032  19.301422  
3033  19.301423  

[3034 rows x 11 columns]

### 5.2 Determine navigation depth over track 

In [26]:
# determine in- or outbound
direction = dict()
vessel_names = df_newlog['Vessel name'].unique()
for vessel_name in vessel_names: 
    vessel_trip = df_newlog[df_newlog['Vessel name']==vessel_name]
    lon_start = vessel_trip['From geometry'].iloc[0].x
    lon_end = vessel_trip['From geometry'].iloc[-1].x
    if lon_start < lon_end: 
        direction[vessel_name] = 'inbound'
    else: 
        direction[vessel_name] = 'outbound'

In [27]:
def determine_UKC(T, FG, iodir): 
    
    if T < 17.4: 
        UKC_a = FG.edges[edge]['UKC_a (T<17.4)']
    else: 
        UKC_a = FG.edges[edge]['UKC_a (T>=17.4)']

    if iodir == 'inbound': 
        UKC_b = FG.edges[edge]['UKC_b (inbound)']
    else: 
        UKC_b = FG.edges[edge]['UKC_b (outbound)']

    return UKC_a + UKC_b*vessel_draught

In [28]:
df_newlog['Req depth'] = ''

for i in df_newlog.index: 
    vessel_name = df_newlog['Vessel name'].loc[i]
    vessel_data = df_trips[df_trips['shipname'] == vessel_name]
    vessel_draught = vessel_data['draughtMarine'].iloc[0]

    edge = (df_newlog['From node'].loc[i], df_newlog['To node'].loc[i])

    # UKC 
    UKC = determine_UKC(vessel_draught, FG, direction[vessel_name])

    # FWA 
    FWA = FG.edges[edge]['FWA']*vessel_draught

    # Required depth 
    req_depth = vessel_draught + UKC + FWA
    df_newlog.at[i, 'Req depth'] = req_depth
    

In [29]:
df_newlog

Vessel name Seq    From node      To node Sub edge  \
0      testschip-3799   1  8.86418e+06  8.86626e+06        0   
1      testschip-3799   3  8.86418e+06  8.86626e+06        1   
2      testschip-3799   5  8.86626e+06  8.86429e+06        0   
3      testschip-3799   7  8.86429e+06  8.86102e+06        0   
4      testschip-3799   9  8.86102e+06   8.8607e+06        0   
...               ...  ..          ...          ...      ...   
3029  testschip-12440  77     S14716_B  8.86446e+06        3   
3030  testschip-12440  79  8.86446e+06  8.86292e+06        0   
3031  testschip-12440  81  8.86292e+06  8.86427e+06        0   
3032  testschip-12440  83  8.86292e+06  8.86427e+06        1   
3033  testschip-12440  85  8.86292e+06  8.86427e+06        2   

                      Timestamp                              From geometry  \
0    2019-01-02 07:28:00.000000  POINT (4.06577726721752 51.9616878496712)   
1    2019-01-02 07:28:37.377858  POINT (4.07100475643483 51.9620610945492)   
2    2019-01-02 07:29:45.827771  POINT (4.08059629478063 51.9614848708232)   
3    2019-01-02 07:30:29.459412  POINT (4.08588733128925 51.9611749800546)   
4    2019-01-02 07:31:16.708295  POINT (4.08745551582984 51.9653093741552)   
...                         ...                                        ...   
3029 2019-01-16 05:21:03.000968  POINT (4.12542158771241 51.9731028973176)   
3030 2019-01-16 05:21:07.351999  POINT (4.12423582717078 51.9734347697144)   
3031 2019-01-16 05:21:12.661157  POINT (4.12285425403692 51.9738214268566)   
3032 2019-01-16 05:22:14.010849  POINT (4.10714114771394 51.9781909994644)   
3033 2019-01-16 05:23:42.182713   POINT (4.0841372668255 51.9838622952073)   

                                    To geometry   Duration     Distance  \
0     POINT (4.07100475643483 51.9620610945492)  37.377858   361.710519   
1     POINT (4.08059629478063 51.9614848708232)  68.449913   662.398934   
2     POINT (4.08588733128925 51.9611749800546)  43.631641   365.321756   
3     POINT (4.08745551582984 51.9653093741552)  47.248883   472.479456   
4     POINT (4.09002397683758 51.9721065878619)  65.190782   776.630463   
...                                         ...        ...          ...   
3029  POINT (4.12423582717078 51.9734347697144)   4.351031    89.460773   
3030  POINT (4.12285425403692 51.9738214268566)   5.309158   104.232441   
3031  POINT (4.10714114771394 51.9781909994644)  61.349692  1184.136286   
3032   POINT (4.0841372668255 51.9838622952073)  88.171864  1701.842355   
3033  POINT (4.08355198540297 51.9839636810505)   2.163717    41.762818   

          Speed Req depth  
0      9.677133    10.898  
1      9.677133    10.898  
2      8.372863    10.898  
3      9.999802    10.898  
4     11.913194    10.898  
...         ...       ...  
3029  20.560822      9.99  
3030  19.632575      9.99  
3031  19.301422      9.99  
3032  19.301422      9.99  
3033  19.301423      9.99  

[3034 rows x 12 columns]

### 5.3 Determine available depth

In [30]:
# defined path
path1= [(3.939957955924711,52.02191583359731), #begin approaches
        (4.049618437170281,51.99131236482086), #end approaches
        (4.118784658437804,51.97562798626344),
        (4.154716312957065,51.95962835860685),
        (4.198841020888635,51.93823137190358),
        (4.220308700300929,51.9302898518613),
        (4.242869913043052,51.91418583835263),
        (4.275374658810644,51.90157562644534),
        (4.293379624950282,51.89688677716952),
        (4.303887861126173,51.89477603487619),
        (4.309308884266536,51.88746173227744),
        (4.307954155783563,51.88073044972657),
        (4.309596108530709,51.87699002773771),
        (4.311663762712838,51.87725215582331)]

mbl = [-2430, -1620, -1620, -1620, -1620, -1640, -1640, -1640, -1640, -1590, -1590, -1590, -1590]

In [31]:
# translate path to edges
df_MBL = pd.DataFrame(index=range(len(path1)-1), columns=['from_geo', 'to_geo', 'geometry', 'mbl'])

for inode, node in enumerate(path1[1:]):
    df_MBL['from_geo'].iloc[inode-1] = path1[inode-1]
    df_MBL['to_geo'].iloc[inode-1] = path1[inode]
    df_MBL['mbl'].iloc[inode-1] = mbl[inode-1] 
    df_MBL['geometry'].iloc[inode-1] = shapely.geometry.LineString([path1[inode-1], path1[inode]])

In [32]:
def find_closest_edgeS(df_MBL, FG, node):
    """find the closest edge on the graph from a given point"""
    
    point = FG.nodes[node]['geometry']
    distance = np.full((len(df_MBL)), fill_value=np.nan)
    for ii, e in enumerate(df_MBL['geometry']):
        distance[ii] = point.distance(e)
    name_edge = list(df_MBL.index)[np.argmin(distance)]
    distance_edge = np.min(distance)
    
    return name_edge, distance_edge

In [34]:
# extract nodes from FG enroute to 3e pet 
nodes = list(set(list(df_newlog['From node'].unique()) + list(df_newlog['To node'].unique())))

# for each node in this subgraph, determine mbl based on closest node in sanders graph 
names = []

for node in nodes: 
    name_edge, distance_edge = find_closest_edgeS(df_MBL, FG, node)
    names.append(name_edge)

# for each edge in FG, check info for its nodes and assign mbl to edge 
for edge in FG.edges: 
    if (edge[0] in nodes) and (edge[1] in nodes):
        #print(edge)
        n0 = names[nodes.index(edge[0])]
        n1 = names[nodes.index(edge[1])]
        
        if n0 == n1: 
            FG.edges[edge]['bedlevel'] = df_MBL.at[n0, 'mbl']
        else: 
            if df_MBL.at[n0, 'mbl'] > df_MBL.at[n1, 'mbl']: 
                FG.edges[edge]['bedlevel'] = df_MBL.at[n0, 'mbl']
            else: 
                FG.edges[edge]['bedlevel'] = df_MBL.at[n1, 'mbl']


In [36]:
def find_waterlevel(timex, timelist, wllist):
    timezone = pytz.timezone("UTC")
    for i, t in enumerate(timelist): 
        if t > timezone.localize(timex):
            break
    return wllist[i]

In [37]:
df_newlog['Av depth'] = ''

for i in df_newlog.index: 
    edge = (df_newlog['From node'].loc[i], df_newlog['To node'].loc[i])
    
    # MBL 
    MBL = FG.edges[edge]['bedlevel']
    
    # Water level 
    t = find_waterlevel(df_newlog['Timestamp'].iloc[i], FG.edges[edge]['time'], FG.edges[edge]['PH10'])
    
    # Available depth
    av_depth = -MBL + t
    df_newlog.at[i, 'Av depth'] = av_depth/100
    
df_newlog['margin'] = df_newlog['Av depth'] - df_newlog['Req depth']

In [38]:
df_newlog

Vessel name Seq    From node      To node Sub edge  \
0      testschip-3799   1  8.86418e+06  8.86626e+06        0   
1      testschip-3799   3  8.86418e+06  8.86626e+06        1   
2      testschip-3799   5  8.86626e+06  8.86429e+06        0   
3      testschip-3799   7  8.86429e+06  8.86102e+06        0   
4      testschip-3799   9  8.86102e+06   8.8607e+06        0   
...               ...  ..          ...          ...      ...   
3029  testschip-12440  77     S14716_B  8.86446e+06        3   
3030  testschip-12440  79  8.86446e+06  8.86292e+06        0   
3031  testschip-12440  81  8.86292e+06  8.86427e+06        0   
3032  testschip-12440  83  8.86292e+06  8.86427e+06        1   
3033  testschip-12440  85  8.86292e+06  8.86427e+06        2   

                      Timestamp                              From geometry  \
0    2019-01-02 07:28:00.000000  POINT (4.06577726721752 51.9616878496712)   
1    2019-01-02 07:28:37.377858  POINT (4.07100475643483 51.9620610945492)   
2    2019-01-02 07:29:45.827771  POINT (4.08059629478063 51.9614848708232)   
3    2019-01-02 07:30:29.459412  POINT (4.08588733128925 51.9611749800546)   
4    2019-01-02 07:31:16.708295  POINT (4.08745551582984 51.9653093741552)   
...                         ...                                        ...   
3029 2019-01-16 05:21:03.000968  POINT (4.12542158771241 51.9731028973176)   
3030 2019-01-16 05:21:07.351999  POINT (4.12423582717078 51.9734347697144)   
3031 2019-01-16 05:21:12.661157  POINT (4.12285425403692 51.9738214268566)   
3032 2019-01-16 05:22:14.010849  POINT (4.10714114771394 51.9781909994644)   
3033 2019-01-16 05:23:42.182713   POINT (4.0841372668255 51.9838622952073)   

                                    To geometry   Duration     Distance  \
0     POINT (4.07100475643483 51.9620610945492)  37.377858   361.710519   
1     POINT (4.08059629478063 51.9614848708232)  68.449913   662.398934   
2     POINT (4.08588733128925 51.9611749800546)  43.631641   365.321756   
3     POINT (4.08745551582984 51.9653093741552)  47.248883   472.479456   
4     POINT (4.09002397683758 51.9721065878619)  65.190782   776.630463   
...                                         ...        ...          ...   
3029  POINT (4.12423582717078 51.9734347697144)   4.351031    89.460773   
3030  POINT (4.12285425403692 51.9738214268566)   5.309158   104.232441   
3031  POINT (4.10714114771394 51.9781909994644)  61.349692  1184.136286   
3032   POINT (4.0841372668255 51.9838622952073)  88.171864  1701.842355   
3033  POINT (4.08355198540297 51.9839636810505)   2.163717    41.762818   

          Speed Req depth Av depth  
0      9.677133    10.898  15.7029  
1      9.677133    10.898  15.7029  
2      8.372863    10.898  15.7021  
3      9.999802    10.898  15.7161  
4     11.913194    10.898  15.7087  
...         ...       ...      ...  
3029  20.560822      9.99  15.9831  
3030  19.632575      9.99  15.9875  
3031  19.301422      9.99  15.9808  
3032  19.301422      9.99  15.9808  
3033  19.301423      9.99  15.9808  

[3034 rows x 13 columns]

In [76]:
df_newlog[df_newlog['margin'] < 5]['Vessel name'].unique()


array(['testschip-3799', 'testschip-6043', 'testschip-8332',
       'testschip-9265'], dtype=object)

### 5.4 Plot

In [43]:
# Indicate the vessel number 
i_vessel = 4
vessel_names = df_newlog['Vessel name'].unique()
vessel_name = vessel_names[i_vessel]

# Indicate the vessel name
df_vessel = df_newlog[df_newlog['Vessel name'] == vessel_name]

In [53]:
colors_palette = ['red', 'blue', 'green', 'purple', 'orange', 'darkred','darkblue', 'darkgreen', 'cadetblue', 
                  'darkpurple', 'white', 'pink', 'lightblue', 'lightgreen', 'gray', 'black', 'lightgray']
colors_jet = ['darkred', 'red', 'orange', 'yellow', 'lightgreen', 'green', 'blue']

In [51]:
def get_line_color_scale(parameter, min_par, max_par, 
                         colorset=['moccasin', 'yellow', 'gold', 'goldenrod', 'orange', 'orangered', 'red', 'darkred']): 
    
    tint = []
    totalrange = max_par - min_par 
    nr_of_bins = len(colorset)
    size_bins = totalrange/nr_of_bins

    if parameter < min_par: 
        tint = colorset[0]
    elif parameter > max_par: 
        tint = colorset[-1]
    else: 
        for ibin in range(nr_of_bins): 
            min_bin = min_par + size_bins * ibin
            max_bin = min_par + size_bins *(ibin+1)
            if min_bin <= parameter <= max_bin: 
                tint = colorset[ibin]
        
    return tint

In [86]:
# Indicate the vessel number 
# i_vessel = 4
# vessel_names = df_newlog['Vessel name'].unique()
# vessel_name = vessel_names[i_vessel]

# Indicate the vessel name
crit_vess = ['testschip-3799', 'testschip-6043', 'testschip-8332', 'testschip-9265']
vessel_name = crit_vess[3]

df_vessel = df_newlog[df_newlog['Vessel name'] == vessel_name]

# Plot the network 
m = folium.Map(location=[51.9, 4.3], zoom_start = 11, tiles="cartodbpositron")

# plot all edges
for edge in FG.edges(data = True):
    points_x = list(edge[2]["geometry"].coords.xy[0])
    points_y = list(edge[2]["geometry"].coords.xy[1])
    
    line = []
    for i, _ in enumerate(points_x):
        line.append((points_y[i], points_x[i]))
        
    folium.PolyLine(line, weight = 2, popup = (edge[2]["StartJunctionId"], edge[2]["EndJunctionId"])).add_to(m)

# plot the edges on the route
for i in df_vessel.index: 
    edge = (df_vessel['From node'].loc[i], df_vessel['To node'].loc[i])
    margin = df_vessel['Av depth'].loc[i] - df_vessel['Req depth'].loc[i]
    margin_color = get_line_color_scale(margin, 0, 10, colors_jet)
    
    route = list(zip(list(df_vessel['From geometry']), list(df_vessel['To geometry'])))
    
    df_vessel['From geometry'].loc[i]
    
    line = [(df_vessel['From geometry'].loc[i].y, df_vessel['From geometry'].loc[i].x), (df_vessel['To geometry'].loc[i].y, df_vessel['To geometry'].loc[i].x)]
    folium.PolyLine(line, color=margin_color, weight=2, popup=margin).add_to(m)
    
m 

In [44]:
# Plot the network 
route = list(zip(list(df_vessel['From geometry']), list(df_vessel['To geometry'])))
m = folium.Map(location=[51.9, 4.3], zoom_start = 11, tiles="cartodbpositron")

for edge in FG.edges(data = True):
    points_x = list(edge[2]["geometry"].coords.xy[0])
    points_y = list(edge[2]["geometry"].coords.xy[1])
    
    line = []
    for i, _ in enumerate(points_x):
        line.append((points_y[i], points_x[i]))
        
    folium.PolyLine(line, weight = 2, popup = (edge[2]["StartJunctionId"], edge[2]["EndJunctionId"])).add_to(m)

for segm in route: 
    line = [(segm[0].y, segm[0].x), (segm[1].y, segm[1].x)]
    folium.PolyLine(line, color = 'orange', weight = 2, popup = (edge[2]["StartJunctionId"], edge[2]["EndJunctionId"])).add_to(m)

m